## This is a note experimenting on the robustness to kernel width of LIME and BayLIME
22/07/2020 XZ

In [1]:
import sys
sys.path.append("..")# allow the notebook to find the parent folder
from sklearn.datasets import load_boston,load_breast_cancer
import sklearn.ensemble
import sklearn.linear_model
import sklearn.model_selection
import numpy as np
from sklearn.metrics import r2_score
np.random.seed(1)
import lime
import lime.lime_tabular
from lime import submodular_pick
from lime import calculate_posteriors
from scipy import stats
import random
import math
import csv


#load example dataset
boston = load_boston()
#cancer= load_breast_cancer()

#print a description of the variables
print(boston.DESCR)
#print(cancer.DESCR)

#train a regressor
rf = sklearn.ensemble.RandomForestRegressor(n_estimators=1000)
train, test, labels_train, labels_test = sklearn.model_selection.train_test_split(boston.data, boston.target, train_size=0.80, test_size=0.20)
rf.fit(train, labels_train);

#train a classifier
# rf = sklearn.ensemble.RandomForestClassifier(n_estimators=1000)
# train, test, labels_train, labels_test = sklearn.model_selection.train_test_split(cancer.data, cancer.target, train_size=0.80, test_size=0.20)
# rf.fit(train, labels_train);

.. _boston_dataset:

Boston house prices dataset
---------------------------

**Data Set Characteristics:**  

    :Number of Instances: 506 

    :Number of Attributes: 13 numeric/categorical predictive. Median Value (attribute 14) is usually the target.

    :Attribute Information (in order):
        - CRIM     per capita crime rate by town
        - ZN       proportion of residential land zoned for lots over 25,000 sq.ft.
        - INDUS    proportion of non-retail business acres per town
        - CHAS     Charles River dummy variable (= 1 if tract bounds river; 0 otherwise)
        - NOX      nitric oxides concentration (parts per 10 million)
        - RM       average number of rooms per dwelling
        - AGE      proportion of owner-occupied units built prior to 1940
        - DIS      weighted distances to five Boston employment centres
        - RAD      index of accessibility to radial highways
        - TAX      full-value property-tax rate per $10,000
        - PTRATIO  pu

In [2]:
# generate an "explainer" object
categorical_features  = np.argwhere(np.array([len(set(boston.data[:,x])) for x in range(boston.data.shape[1])]) <= 10).flatten()



# Now you can play with different kernel_width to see how the resutls change...
explainer = lime.lime_tabular.LimeTabularExplainer(train, feature_names=boston.feature_names, 
                                                   class_names=['price'], categorical_features=categorical_features, 
                                                    verbose=False, mode='regression',
                                                   discretize_continuous=False,feature_selection='none',
                                                   sample_around_instance=False,kernel_width=5)



#generate an explanation for testing..
instance = 13
#use rf.predict_proba for classfication 
exp = explainer.explain_instance(test[instance], rf.predict,#num_features=13,
                                 model_regressor='non_Bay',
                                 num_samples=1000,
                                 #labels=labels_test[i],
                                 )#'non_Bay' 'Bay_non_info_prior' 'Bay_info_prior' 'BayesianRidge_inf_prior_fit_alpha'

exp.show_in_notebook(show_table=True)
#fig = exp.as_pyplot_figure(label=1)


exp = explainer.explain_instance(test[instance], rf.predict,#num_features=13,
                                 model_regressor='Bay_info_prior',
                                 num_samples=1000,
                                 #labels=labels_test[i],
                                 )#'non_Bay' 'Bay_non_info_prior' 'Bay_info_prior' 'BayesianRidge_inf_prior_fit_alpha'


alpha_init=1
lambda_init=1
with open('.\posterior_configure.csv') as csv_file:
    csv_reader=csv.reader(csv_file)
    line_count = 0
    for row in csv_reader:
        if line_count == 1:
            alpha_init=float(row[0])
            lambda_init=float(row[1])
        line_count=line_count+1
    
exp.show_in_notebook(show_table=True)

using non_Bay option for model regressor


using Bay_info_prior option for model regressor
the alpha is 0.1
the lambda is 20.0
the regulation term lambda/alpha is 200.0


In [3]:
# define the global lipschitz function
def glo_lip (kw1, kw2, f1, f2):
    f1=np.array(f1)
    f2=np.array(f2)
    return np.linalg.norm(f1-f2)/np.linalg.norm(kw1-kw2)
print(glo_lip(2,4,[0.1,0.2,0.4,0.1],[0.2,0.2,0.1,0.1]))

0.158113883008419


In [ ]:
i=1
kw1_s=np.array([])
kw2_s=np.array([])
lip_s=np.array([])
while i<=5000:
    kw1=random.uniform(0.01,5)
    kw1_s=np.append(kw1_s,kw1)
    kw2=random.uniform(0.01,5)
    kw2_s=np.append(kw2_s,kw2)
    
    explainer = lime.lime_tabular.LimeTabularExplainer(train, feature_names=boston.feature_names, 
                                                   class_names=['price'], categorical_features=categorical_features, 
                                                    verbose=False, mode='regression',
                                                   discretize_continuous=False,feature_selection='none',
                                                   sample_around_instance=False,kernel_width=kw1)
    #generate an explanation for testing..
    instance = 13
    #use rf.predict_proba for classfication 
    exp = explainer.explain_instance(test[instance], rf.predict,#num_features=13,
                                 model_regressor='Bay_non_info_prior',
                                 num_samples=1000,
                                 #labels=labels_test[i],
                                 )#'non_Bay' 'Bay_non_info_prior' 'Bay_info_prior'
    
    temp=exp.as_list()
    temp = sorted(temp, key=lambda a_entry: a_entry[0])
    temp=np.delete(temp,0,axis=1).flatten()
    f1=[float(i) for i in temp]
    
    explainer = lime.lime_tabular.LimeTabularExplainer(train, feature_names=boston.feature_names, 
                                                   class_names=['price'], categorical_features=categorical_features, 
                                                    verbose=False, mode='regression',
                                                   discretize_continuous=False,feature_selection='none',
                                                   sample_around_instance=False,kernel_width=kw2)
    #generate an explanation for testing..
    instance = 13
    #use rf.predict_proba for classfication 
    exp = explainer.explain_instance(test[instance], rf.predict,#num_features=13,
                                 model_regressor='Bay_non_info_prior',
                                 num_samples=1000,
                                 #labels=labels_test[i],
                                 )#'non_Bay' 'Bay_non_info_prior' 'Bay_info_prior'
    
    temp=exp.as_list()
    temp = sorted(temp, key=lambda a_entry: a_entry[0])
    temp=np.delete(temp,0,axis=1).flatten()
    f2=[float(i) for i in temp]
    
    lip=glo_lip(kw1, kw2, f1, f2)
    lip_s=np.append(lip_s,lip)
    
    i=i+1
    
print(stats.describe(lip_s))
data=np.asarray((kw1_s,kw2_s,lip_s)).T
np.savetxt("./figures/robust_kw/raw_data/3d_plot_Bay_non_info_prior.csv", data, delimiter=",")

using Bay_non_info_prior option for model regressor
Convergence after  3  iterations
the alpha is 4.695077376712538
the lambda is 0.5627652495452765
the regulation term lambda/alpha is 0.11986282746618353
using Bay_non_info_prior option for model regressor
Convergence after  3  iterations
the alpha is 0.15531957887662698
the lambda is 0.5050374822719643
the regulation term lambda/alpha is 3.251602186438609
using Bay_non_info_prior option for model regressor
Convergence after  3  iterations
the alpha is 0.20137109320617766
the lambda is 0.4790792794665352
the regulation term lambda/alpha is 2.379086649621655
using Bay_non_info_prior option for model regressor
Convergence after  3  iterations
the alpha is 0.5317214242634074
the lambda is 0.5382310333197349
the regulation term lambda/alpha is 1.0122425179037036
using Bay_non_info_prior option for model regressor
Convergence after  3  iterations
the alpha is 0.15008447188391147
the lambda is 0.4915346840647694
the regulation term lambda/al

In [ ]:

i=1
kw1_s=np.array([])
kw2_s=np.array([])
lip_s=np.array([])
while i<=5000:
    kw1=random.uniform(0.01,5)
    kw1_s=np.append(kw1_s,kw1)
    kw2=random.uniform(0.01,5)
    kw2_s=np.append(kw2_s,kw2)
    
    explainer = lime.lime_tabular.LimeTabularExplainer(train, feature_names=boston.feature_names, 
                                                   class_names=['price'], categorical_features=categorical_features, 
                                                    verbose=False, mode='regression',
                                                   discretize_continuous=False,feature_selection='none',
                                                   sample_around_instance=False,kernel_width=kw1)
    #generate an explanation for testing..
    instance = 13
    #use rf.predict_proba for classfication 
    exp = explainer.explain_instance(test[instance], rf.predict,#num_features=13,
                                 model_regressor='non_Bay',
                                 num_samples=1000,
                                 #labels=labels_test[i],
                                 )#'non_Bay' 'Bay_non_info_prior' 'Bay_info_prior' BayesianRidge_inf_prior_fit_alpha
    
    temp=exp.as_list()
    temp = sorted(temp, key=lambda a_entry: a_entry[0])
    temp=np.delete(temp,0,axis=1).flatten()
    f1=[float(i) for i in temp]
    
    explainer = lime.lime_tabular.LimeTabularExplainer(train, feature_names=boston.feature_names, 
                                                   class_names=['price'], categorical_features=categorical_features, 
                                                    verbose=False, mode='regression',
                                                   discretize_continuous=False,feature_selection='none',
                                                   sample_around_instance=False,kernel_width=kw2)
    #generate an explanation for testing..
    instance = 13
    #use rf.predict_proba for classfication 
    exp = explainer.explain_instance(test[instance], rf.predict,#num_features=13,
                                 model_regressor='non_Bay',
                                 num_samples=1000,
                                 #labels=labels_test[i],
                                 )#'non_Bay' 'Bay_non_info_prior' 'Bay_info_prior' BayesianRidge_inf_prior_fit_alpha
    
    temp=exp.as_list()
    temp = sorted(temp, key=lambda a_entry: a_entry[0])
    temp=np.delete(temp,0,axis=1).flatten()
    f2=[float(i) for i in temp]
    
    lip=glo_lip(kw1, kw2, f1, f2)
    lip_s=np.append(lip_s,lip)
    
    i=i+1
    
print(stats.describe(lip_s))
data=np.asarray((kw1_s,kw2_s,lip_s)).T
np.savetxt("./figures/robust_kw/raw_data/3d_plot_non_Bay.csv", data, delimiter=",")

In [13]:

i=1
kw1_s=np.array([])
kw2_s=np.array([])
lip_s=np.array([])
while i<=5000:
    kw1=random.uniform(0.01,5)
    kw1_s=np.append(kw1_s,kw1)
    kw2=random.uniform(0.01,5)
    kw2_s=np.append(kw2_s,kw2)
    
    explainer = lime.lime_tabular.LimeTabularExplainer(train, feature_names=boston.feature_names, 
                                                   class_names=['price'], categorical_features=categorical_features, 
                                                    verbose=False, mode='regression',
                                                   discretize_continuous=False,feature_selection='none',
                                                   sample_around_instance=False,kernel_width=kw1)
    #generate an explanation for testing..
    instance = 13
    #use rf.predict_proba for classfication 
    exp = explainer.explain_instance(test[instance], rf.predict,#num_features=13,
                                 model_regressor='Bay_info_prior',
                                 num_samples=1000,
                                 #labels=labels_test[i],
                                 )#'non_Bay' 'Bay_non_info_prior' 'Bay_info_prior' BayesianRidge_inf_prior_fit_alpha
    
    alpha_init=1
    lambda_init=1
    with open('.\posterior_configure.csv') as csv_file:
        csv_reader=csv.reader(csv_file)
        line_count = 0
        for row in csv_reader:
            if line_count == 1:
                alpha_init=float(row[0])
                lambda_init=float(row[1])
            line_count=line_count+1
        
    temp=exp.as_list()
    temp = sorted(temp, key=lambda a_entry: a_entry[0])
    temp=np.delete(temp,0,axis=1).flatten()
    f1=[float(i) for i in temp]
    
    explainer = lime.lime_tabular.LimeTabularExplainer(train, feature_names=boston.feature_names, 
                                                   class_names=['price'], categorical_features=categorical_features, 
                                                    verbose=False, mode='regression',
                                                   discretize_continuous=False,feature_selection='none',
                                                   sample_around_instance=False,kernel_width=kw2)
    #generate an explanation for testing..
    instance = 13
    #use rf.predict_proba for classfication 
    exp = explainer.explain_instance(test[instance], rf.predict,#num_features=13,
                                 model_regressor='Bay_info_prior',
                                 num_samples=1000,
                                 #labels=labels_test[i],
                                 )#'non_Bay' 'Bay_non_info_prior' 'Bay_info_prior' BayesianRidge_inf_prior_fit_alpha
    
    alpha_init=1
    lambda_init=1
    with open('.\posterior_configure.csv') as csv_file:
        csv_reader=csv.reader(csv_file)
        line_count = 0
        for row in csv_reader:
            if line_count == 1:
                alpha_init=float(row[0])
                lambda_init=float(row[1])
            line_count=line_count+1
    
    
    temp=exp.as_list()
    temp = sorted(temp, key=lambda a_entry: a_entry[0])
    temp=np.delete(temp,0,axis=1).flatten()
    f2=[float(i) for i in temp]
    
    lip=glo_lip(kw1, kw2, f1, f2)
    lip_s=np.append(lip_s,lip)
    
    i=i+1
    
print(stats.describe(lip_s))
data=np.asarray((kw1_s,kw2_s,lip_s)).T
np.savetxt("./figures/robust_kw/raw_data/3d_plot_Bay_info_prior_a1_l200.csv", data, delimiter=",")

using Bay_info_prior option for model regressor
the alpha is 1.0
the lambda is 200.0
the regulation term lambda/alpha is 200.0
using Bay_info_prior option for model regressor
the alpha is 1.0
the lambda is 200.0
the regulation term lambda/alpha is 200.0
using Bay_info_prior option for model regressor
the alpha is 1.0
the lambda is 200.0
the regulation term lambda/alpha is 200.0
using Bay_info_prior option for model regressor
the alpha is 1.0
the lambda is 200.0
the regulation term lambda/alpha is 200.0
using Bay_info_prior option for model regressor
the alpha is 1.0
the lambda is 200.0
the regulation term lambda/alpha is 200.0
using Bay_info_prior option for model regressor
the alpha is 1.0
the lambda is 200.0
the regulation term lambda/alpha is 200.0
using Bay_info_prior option for model regressor
the alpha is 1.0
the lambda is 200.0
the regulation term lambda/alpha is 200.0
using Bay_info_prior option for model regressor
the alpha is 1.0
the lambda is 200.0
the regulation term lambda

using Bay_info_prior option for model regressor
the alpha is 1.0
the lambda is 200.0
the regulation term lambda/alpha is 200.0
using Bay_info_prior option for model regressor
the alpha is 1.0
the lambda is 200.0
the regulation term lambda/alpha is 200.0
using Bay_info_prior option for model regressor
the alpha is 1.0
the lambda is 200.0
the regulation term lambda/alpha is 200.0
using Bay_info_prior option for model regressor
the alpha is 1.0
the lambda is 200.0
the regulation term lambda/alpha is 200.0
using Bay_info_prior option for model regressor
the alpha is 1.0
the lambda is 200.0
the regulation term lambda/alpha is 200.0
using Bay_info_prior option for model regressor
the alpha is 1.0
the lambda is 200.0
the regulation term lambda/alpha is 200.0
using Bay_info_prior option for model regressor
the alpha is 1.0
the lambda is 200.0
the regulation term lambda/alpha is 200.0
using Bay_info_prior option for model regressor
the alpha is 1.0
the lambda is 200.0
the regulation term lambda

using Bay_info_prior option for model regressor
the alpha is 1.0
the lambda is 200.0
the regulation term lambda/alpha is 200.0
using Bay_info_prior option for model regressor
the alpha is 1.0
the lambda is 200.0
the regulation term lambda/alpha is 200.0
using Bay_info_prior option for model regressor
the alpha is 1.0
the lambda is 200.0
the regulation term lambda/alpha is 200.0
using Bay_info_prior option for model regressor
the alpha is 1.0
the lambda is 200.0
the regulation term lambda/alpha is 200.0
using Bay_info_prior option for model regressor
the alpha is 1.0
the lambda is 200.0
the regulation term lambda/alpha is 200.0
using Bay_info_prior option for model regressor
the alpha is 1.0
the lambda is 200.0
the regulation term lambda/alpha is 200.0
using Bay_info_prior option for model regressor
the alpha is 1.0
the lambda is 200.0
the regulation term lambda/alpha is 200.0
using Bay_info_prior option for model regressor
the alpha is 1.0
the lambda is 200.0
the regulation term lambda

using Bay_info_prior option for model regressor
the alpha is 1.0
the lambda is 200.0
the regulation term lambda/alpha is 200.0
using Bay_info_prior option for model regressor
the alpha is 1.0
the lambda is 200.0
the regulation term lambda/alpha is 200.0
using Bay_info_prior option for model regressor
the alpha is 1.0
the lambda is 200.0
the regulation term lambda/alpha is 200.0
using Bay_info_prior option for model regressor
the alpha is 1.0
the lambda is 200.0
the regulation term lambda/alpha is 200.0
using Bay_info_prior option for model regressor
the alpha is 1.0
the lambda is 200.0
the regulation term lambda/alpha is 200.0
using Bay_info_prior option for model regressor
the alpha is 1.0
the lambda is 200.0
the regulation term lambda/alpha is 200.0
using Bay_info_prior option for model regressor
the alpha is 1.0
the lambda is 200.0
the regulation term lambda/alpha is 200.0
using Bay_info_prior option for model regressor
the alpha is 1.0
the lambda is 200.0
the regulation term lambda

using Bay_info_prior option for model regressor
the alpha is 1.0
the lambda is 200.0
the regulation term lambda/alpha is 200.0
using Bay_info_prior option for model regressor
the alpha is 1.0
the lambda is 200.0
the regulation term lambda/alpha is 200.0
using Bay_info_prior option for model regressor
the alpha is 1.0
the lambda is 200.0
the regulation term lambda/alpha is 200.0
using Bay_info_prior option for model regressor
the alpha is 1.0
the lambda is 200.0
the regulation term lambda/alpha is 200.0
using Bay_info_prior option for model regressor
the alpha is 1.0
the lambda is 200.0
the regulation term lambda/alpha is 200.0
using Bay_info_prior option for model regressor
the alpha is 1.0
the lambda is 200.0
the regulation term lambda/alpha is 200.0
using Bay_info_prior option for model regressor
the alpha is 1.0
the lambda is 200.0
the regulation term lambda/alpha is 200.0
using Bay_info_prior option for model regressor
the alpha is 1.0
the lambda is 200.0
the regulation term lambda

...

using Bay_info_prior option for model regressor
the alpha is 1.0
the lambda is 200.0
the regulation term lambda/alpha is 200.0
using Bay_info_prior option for model regressor
the alpha is 1.0
the lambda is 200.0
the regulation term lambda/alpha is 200.0
using Bay_info_prior option for model regressor
the alpha is 1.0
the lambda is 200.0
the regulation term lambda/alpha is 200.0
using Bay_info_prior option for model regressor
the alpha is 1.0
the lambda is 200.0
the regulation term lambda/alpha is 200.0
using Bay_info_prior option for model regressor
the alpha is 1.0
the lambda is 200.0
the regulation term lambda/alpha is 200.0
using Bay_info_prior option for model regressor
the alpha is 1.0
the lambda is 200.0
the regulation term lambda/alpha is 200.0
using Bay_info_prior option for model regressor
the alpha is 1.0
the lambda is 200.0
the regulation term lambda/alpha is 200.0
using Bay_info_prior option for model regressor
the alpha is 1.0
the lambda is 200.0
the regulation term lambda

using Bay_info_prior option for model regressor
the alpha is 1.0
the lambda is 200.0
the regulation term lambda/alpha is 200.0
using Bay_info_prior option for model regressor
the alpha is 1.0
the lambda is 200.0
the regulation term lambda/alpha is 200.0
using Bay_info_prior option for model regressor
the alpha is 1.0
the lambda is 200.0
the regulation term lambda/alpha is 200.0
using Bay_info_prior option for model regressor
the alpha is 1.0
the lambda is 200.0
the regulation term lambda/alpha is 200.0
using Bay_info_prior option for model regressor
the alpha is 1.0
the lambda is 200.0
the regulation term lambda/alpha is 200.0
using Bay_info_prior option for model regressor
the alpha is 1.0
the lambda is 200.0
the regulation term lambda/alpha is 200.0
using Bay_info_prior option for model regressor
the alpha is 1.0
the lambda is 200.0
the regulation term lambda/alpha is 200.0
using Bay_info_prior option for model regressor
the alpha is 1.0
the lambda is 200.0
the regulation term lambda

the alpha is 1.0
the lambda is 200.0
the regulation term lambda/alpha is 200.0
using Bay_info_prior option for model regressor
the alpha is 1.0
the lambda is 200.0
the regulation term lambda/alpha is 200.0
using Bay_info_prior option for model regressor
the alpha is 1.0
the lambda is 200.0
the regulation term lambda/alpha is 200.0
using Bay_info_prior option for model regressor
the alpha is 1.0
the lambda is 200.0
the regulation term lambda/alpha is 200.0
using Bay_info_prior option for model regressor
the alpha is 1.0
the lambda is 200.0
the regulation term lambda/alpha is 200.0
using Bay_info_prior option for model regressor
the alpha is 1.0
the lambda is 200.0
the regulation term lambda/alpha is 200.0
using Bay_info_prior option for model regressor
the alpha is 1.0
the lambda is 200.0
the regulation term lambda/alpha is 200.0
using Bay_info_prior option for model regressor
the alpha is 1.0
the lambda is 200.0
the regulation term lambda/alpha is 200.0
using Bay_info_prior option for 

using Bay_info_prior option for model regressor
the alpha is 1.0
the lambda is 200.0
the regulation term lambda/alpha is 200.0
using Bay_info_prior option for model regressor
the alpha is 1.0
the lambda is 200.0
the regulation term lambda/alpha is 200.0
using Bay_info_prior option for model regressor
the alpha is 1.0
the lambda is 200.0
the regulation term lambda/alpha is 200.0
using Bay_info_prior option for model regressor
the alpha is 1.0
the lambda is 200.0
the regulation term lambda/alpha is 200.0
using Bay_info_prior option for model regressor
the alpha is 1.0
the lambda is 200.0
the regulation term lambda/alpha is 200.0
using Bay_info_prior option for model regressor
the alpha is 1.0
the lambda is 200.0
the regulation term lambda/alpha is 200.0
using Bay_info_prior option for model regressor
the alpha is 1.0
the lambda is 200.0
the regulation term lambda/alpha is 200.0
using Bay_info_prior option for model regressor
the alpha is 1.0
the lambda is 200.0
the regulation term lambda

using Bay_info_prior option for model regressor
the alpha is 1.0
the lambda is 200.0
the regulation term lambda/alpha is 200.0
using Bay_info_prior option for model regressor
the alpha is 1.0
the lambda is 200.0
the regulation term lambda/alpha is 200.0
using Bay_info_prior option for model regressor
the alpha is 1.0
the lambda is 200.0
the regulation term lambda/alpha is 200.0
using Bay_info_prior option for model regressor
the alpha is 1.0
the lambda is 200.0
the regulation term lambda/alpha is 200.0
using Bay_info_prior option for model regressor
the alpha is 1.0
the lambda is 200.0
the regulation term lambda/alpha is 200.0
using Bay_info_prior option for model regressor
the alpha is 1.0
the lambda is 200.0
the regulation term lambda/alpha is 200.0
using Bay_info_prior option for model regressor
the alpha is 1.0
the lambda is 200.0
the regulation term lambda/alpha is 200.0
using Bay_info_prior option for model regressor
the alpha is 1.0
the lambda is 200.0
the regulation term lambda

In [9]:

i=1
kw1_s=np.array([])
kw2_s=np.array([])
lip_s=np.array([])
while i<=5000:
    kw1=random.uniform(0.01,5)
    kw1_s=np.append(kw1_s,kw1)
    kw2=random.uniform(0.01,5)
    kw2_s=np.append(kw2_s,kw2)
    
    explainer = lime.lime_tabular.LimeTabularExplainer(train, feature_names=boston.feature_names, 
                                                   class_names=['price'], categorical_features=categorical_features, 
                                                    verbose=False, mode='regression',
                                                   discretize_continuous=False,feature_selection='none',
                                                   sample_around_instance=False,kernel_width=kw1)
    #generate an explanation for testing..
    instance = 13
    #use rf.predict_proba for classfication 
    exp = explainer.explain_instance(test[instance], rf.predict,#num_features=13,
                                 model_regressor='BayesianRidge_inf_prior_fit_alpha',
                                 num_samples=1000,
                                 #labels=labels_test[i],
                                 )#'non_Bay' 'Bay_non_info_prior' 'Bay_info_prior' BayesianRidge_inf_prior_fit_alpha
    
    alpha_init=1
    lambda_init=1
    with open('.\posterior_configure.csv') as csv_file:
        csv_reader=csv.reader(csv_file)
        line_count = 0
        for row in csv_reader:
            if line_count == 1:
                alpha_init=float(row[0])
                lambda_init=float(row[1])
            line_count=line_count+1
        
    temp=exp.as_list()
    temp = sorted(temp, key=lambda a_entry: a_entry[0])
    temp=np.delete(temp,0,axis=1).flatten()
    f1=[float(i) for i in temp]
    
    explainer = lime.lime_tabular.LimeTabularExplainer(train, feature_names=boston.feature_names, 
                                                   class_names=['price'], categorical_features=categorical_features, 
                                                    verbose=False, mode='regression',
                                                   discretize_continuous=False,feature_selection='none',
                                                   sample_around_instance=False,kernel_width=kw2)
    #generate an explanation for testing..
    instance = 13
    #use rf.predict_proba for classfication 
    exp = explainer.explain_instance(test[instance], rf.predict,#num_features=13,
                                 model_regressor='BayesianRidge_inf_prior_fit_alpha',
                                 num_samples=1000,
                                 #labels=labels_test[i],
                                 )#'non_Bay' 'Bay_non_info_prior' 'Bay_info_prior' BayesianRidge_inf_prior_fit_alpha
    
    alpha_init=1
    lambda_init=1
    with open('.\posterior_configure.csv') as csv_file:
        csv_reader=csv.reader(csv_file)
        line_count = 0
        for row in csv_reader:
            if line_count == 1:
                alpha_init=float(row[0])
                lambda_init=float(row[1])
            line_count=line_count+1
    
    
    temp=exp.as_list()
    temp = sorted(temp, key=lambda a_entry: a_entry[0])
    temp=np.delete(temp,0,axis=1).flatten()
    f2=[float(i) for i in temp]
    
    lip=glo_lip(kw1, kw2, f1, f2)
    lip_s=np.append(lip_s,lip)
    
    i=i+1
    
print(stats.describe(lip_s))
data=np.asarray((kw1_s,kw2_s,lip_s)).T
np.savetxt("./figures/robust_kw/raw_data/3d_plot_BayesianRidge_inf_prior_fit_alpha_l200.csv", data, delimiter=",")

using Bay_info_prior_fixed_lambda_fit_alpha option for model regressor
Convergence after  13  iterations
the alpha is 7709.885285308041
the lambda is 200.0
the regulation term lambda/alpha is 0.025940723188335894
using Bay_info_prior_fixed_lambda_fit_alpha option for model regressor
Convergence after  8  iterations
the alpha is 20.92963971425416
the lambda is 200.0
the regulation term lambda/alpha is 9.555826222072504
using Bay_info_prior_fixed_lambda_fit_alpha option for model regressor
Convergence after  6  iterations
the alpha is 0.07959821231404515
the lambda is 200.0
the regulation term lambda/alpha is 2512.6192433936094
using Bay_info_prior_fixed_lambda_fit_alpha option for model regressor
Convergence after  6  iterations
the alpha is 0.1055844277634519
the lambda is 200.0
the regulation term lambda/alpha is 1894.218723693553
using Bay_info_prior_fixed_lambda_fit_alpha option for model regressor
Convergence after  6  iterations
the alpha is 0.15622587739501267
the lambda is 200.0

using Bay_info_prior_fixed_lambda_fit_alpha option for model regressor
Convergence after  1  iterations
the alpha is 500000001.0
the lambda is 200.0
the regulation term lambda/alpha is 3.999999992e-07
using Bay_info_prior_fixed_lambda_fit_alpha option for model regressor
Convergence after  6  iterations
the alpha is 0.5025681235438727
the lambda is 200.0
the regulation term lambda/alpha is 397.9559996557175
using Bay_info_prior_fixed_lambda_fit_alpha option for model regressor
Convergence after  6  iterations
the alpha is 0.12537664295685563
the lambda is 200.0
the regulation term lambda/alpha is 1595.1934529689363
using Bay_info_prior_fixed_lambda_fit_alpha option for model regressor
Convergence after  6  iterations
the alpha is 1.7426586319405872
the lambda is 200.0
the regulation term lambda/alpha is 114.76717030763753
using Bay_info_prior_fixed_lambda_fit_alpha option for model regressor
Convergence after  5  iterations
the alpha is 0.058998296065368466
the lambda is 200.0
the regu

using Bay_info_prior_fixed_lambda_fit_alpha option for model regressor
Convergence after  6  iterations
the alpha is 0.5248984959726113
the lambda is 200.0
the regulation term lambda/alpha is 381.02604891143716
using Bay_info_prior_fixed_lambda_fit_alpha option for model regressor
Convergence after  6  iterations
the alpha is 2.5628881371752876
the lambda is 200.0
the regulation term lambda/alpha is 78.0369603725397
using Bay_info_prior_fixed_lambda_fit_alpha option for model regressor
Convergence after  2  iterations
the alpha is 499999998.90111697
the lambda is 200.0
the regulation term lambda/alpha is 4.000000008791064e-07
using Bay_info_prior_fixed_lambda_fit_alpha option for model regressor
Convergence after  5  iterations
the alpha is 0.06165311287809241
the lambda is 200.0
the regulation term lambda/alpha is 3243.9562361670673
using Bay_info_prior_fixed_lambda_fit_alpha option for model regressor
Convergence after  6  iterations
the alpha is 0.09534624247958796
the lambda is 200

using Bay_info_prior_fixed_lambda_fit_alpha option for model regressor
Convergence after  6  iterations
the alpha is 0.13557316867844926
the lambda is 200.0
the regulation term lambda/alpha is 1475.2181567309788
using Bay_info_prior_fixed_lambda_fit_alpha option for model regressor
Convergence after  8  iterations
the alpha is 350.0046789926858
the lambda is 200.0
the regulation term lambda/alpha is 0.5714209323589629
using Bay_info_prior_fixed_lambda_fit_alpha option for model regressor
Convergence after  6  iterations
the alpha is 0.12202512843112513
the lambda is 200.0
the regulation term lambda/alpha is 1639.006674866041
using Bay_info_prior_fixed_lambda_fit_alpha option for model regressor
Convergence after  6  iterations
the alpha is 0.23699999114648304
the lambda is 200.0
the regulation term lambda/alpha is 843.8818880646523
using Bay_info_prior_fixed_lambda_fit_alpha option for model regressor
Convergence after  6  iterations
the alpha is 0.1897129353557375
the lambda is 200.0


using Bay_info_prior_fixed_lambda_fit_alpha option for model regressor
Convergence after  6  iterations
the alpha is 0.23691721099526353
the lambda is 200.0
the regulation term lambda/alpha is 844.1767449474088
using Bay_info_prior_fixed_lambda_fit_alpha option for model regressor
Convergence after  6  iterations
the alpha is 0.0765196011367064
the lambda is 200.0
the regulation term lambda/alpha is 2613.7093898684757
using Bay_info_prior_fixed_lambda_fit_alpha option for model regressor
Convergence after  9  iterations
the alpha is 183.66076538938196
the lambda is 200.0
the regulation term lambda/alpha is 1.0889642084196751
using Bay_info_prior_fixed_lambda_fit_alpha option for model regressor
Convergence after  1  iterations
the alpha is 500000001.0
the lambda is 200.0
the regulation term lambda/alpha is 3.999999992e-07
using Bay_info_prior_fixed_lambda_fit_alpha option for model regressor
Convergence after  6  iterations
the alpha is 2.1688220846781054
the lambda is 200.0
the regula

...

Convergence after  6  iterations
the alpha is 0.1280679038407596
the lambda is 200.0
the regulation term lambda/alpha is 1561.6715351934017
using Bay_info_prior_fixed_lambda_fit_alpha option for model regressor
Convergence after  6  iterations
the alpha is 0.106111267679373
the lambda is 200.0
the regulation term lambda/alpha is 1884.8139728602835
using Bay_info_prior_fixed_lambda_fit_alpha option for model regressor
Convergence after  6  iterations
the alpha is 0.2218316940329789
the lambda is 200.0
the regulation term lambda/alpha is 901.5844235957859
using Bay_info_prior_fixed_lambda_fit_alpha option for model regressor
Convergence after  5  iterations
the alpha is 0.061446213821920365
the lambda is 200.0
the regulation term lambda/alpha is 3254.8791464943256
using Bay_info_prior_fixed_lambda_fit_alpha option for model regressor
Convergence after  15  iterations
the alpha is 3397.980264990657
the lambda is 200.0
the regulation term lambda/alpha is 0.05885849369420924
using Bay_info_

using Bay_info_prior_fixed_lambda_fit_alpha option for model regressor
Convergence after  6  iterations
the alpha is 1.062653787873965
the lambda is 200.0
the regulation term lambda/alpha is 188.20805259644996
using Bay_info_prior_fixed_lambda_fit_alpha option for model regressor
Convergence after  6  iterations
the alpha is 0.12668652497934216
the lambda is 200.0
the regulation term lambda/alpha is 1578.6998659298022
using Bay_info_prior_fixed_lambda_fit_alpha option for model regressor
Convergence after  6  iterations
the alpha is 0.0849184493611283
the lambda is 200.0
the regulation term lambda/alpha is 2355.2008015298343
using Bay_info_prior_fixed_lambda_fit_alpha option for model regressor
Convergence after  6  iterations
the alpha is 1.0883161100895036
the lambda is 200.0
the regulation term lambda/alpha is 183.77013640232883
using Bay_info_prior_fixed_lambda_fit_alpha option for model regressor
Convergence after  5  iterations
the alpha is 0.062343406078868374
the lambda is 200.

Convergence after  6  iterations
the alpha is 3.8470974328926335
the lambda is 200.0
the regulation term lambda/alpha is 51.987245836303124
using Bay_info_prior_fixed_lambda_fit_alpha option for model regressor
Convergence after  5  iterations
the alpha is 0.06171783891872666
the lambda is 200.0
the regulation term lambda/alpha is 3240.5541656014666
using Bay_info_prior_fixed_lambda_fit_alpha option for model regressor
Convergence after  6  iterations
the alpha is 390474601.7483776
the lambda is 200.0
the regulation term lambda/alpha is 5.121972059244977e-07
using Bay_info_prior_fixed_lambda_fit_alpha option for model regressor
Convergence after  6  iterations
the alpha is 0.07921634279088119
the lambda is 200.0
the regulation term lambda/alpha is 2524.7315510130134
using Bay_info_prior_fixed_lambda_fit_alpha option for model regressor
Convergence after  1  iterations
the alpha is 500000001.0
the lambda is 200.0
the regulation term lambda/alpha is 3.999999992e-07
using Bay_info_prior_f

using Bay_info_prior_fixed_lambda_fit_alpha option for model regressor
Convergence after  6  iterations
the alpha is 0.20070416402918057
the lambda is 200.0
the regulation term lambda/alpha is 996.4915325370221
using Bay_info_prior_fixed_lambda_fit_alpha option for model regressor
Convergence after  7  iterations
the alpha is 11.007447270195923
the lambda is 200.0
the regulation term lambda/alpha is 18.16951697252511
using Bay_info_prior_fixed_lambda_fit_alpha option for model regressor
Convergence after  6  iterations
the alpha is 0.6484641417434311
the lambda is 200.0
the regulation term lambda/alpha is 308.42106313278805
using Bay_info_prior_fixed_lambda_fit_alpha option for model regressor
Convergence after  7  iterations
the alpha is 82.74453667035752
the lambda is 200.0
the regulation term lambda/alpha is 2.417078009594417
using Bay_info_prior_fixed_lambda_fit_alpha option for model regressor
Convergence after  10  iterations
the alpha is 2160.6141945917393
the lambda is 200.0
th

FileNotFoundError: [Errno 2] No such file or directory: './figures/figures/robust_kw/3d_plot_BayesianRidge_inf_prior_fit_alpha_l200.csv'

In [ ]:
from mpl_toolkits.mplot3d import Axes3D
import matplotlib.pyplot as plt
import math 

print(lip_s)
fig = plt.figure()
ax = fig.add_subplot(111, projection='3d')
Z=np.array([])
for i in np.asarray(lip_s):
    if i!=0:
        Z=np.append(Z,math.log(i))
    else:
        Z=np.append(Z,0)
print(Z)

pnt3d=ax.scatter(kw1_s, kw2_s, Z,c=lip_s,marker='^')

ax.set_xlabel('kw1')
ax.set_ylabel('kw2')
ax.set_zlabel('lip')
ax.set_zlim(-5, 8)
#ax.set_ylim(0, 10)
#ax.set_xlim(0, 10)
cbar=plt.colorbar(pnt3d)

plt.show()

In [10]:
np.savetxt("./figures/robust_kw/raw_data/3d_plot_BayesianRidge_inf_prior_fit_alpha_l200.csv", data, delimiter=",")